# Fitting

There are two built in fitting engines, `lmfit` and `bumps`.

Import all the packages.

In [1]:
# Import all the packages
from easyCore import np
from easyDiffractionLib.sample import Sample
from easyDiffractionLib import Phases
from easyDiffractionLib.interface import InterfaceFactory
from easyDiffractionLib.Elements.Experiments.Experiment import Pars1D
from easyDiffractionLib.Elements.Experiments.Pattern import Pattern1D

from easyCore.Fitting.Fitting import Fitter

from easyCore.Datasets.xarray import xr

GSAS-II binary directory: /home/simonward/.cache/pypoetry/virtualenvs/easydiffractionlib-jQmFKVli-py3.7/src/libslinux/libsLinux/GSASII/bindist


In [2]:
try:
    import hvplot.xarray
except:
    import sys
    !{sys.executable} -m pip install hvplot
    import hvplot.xarray

## Preparing the sample and data

We load up a cif file and then set the experimental parameters.

In [3]:
interface = InterfaceFactory()
c = Phases.from_cif_file('PbSO4.cif')
S = Sample(phases=c, parameters=Pars1D.default(), pattern=Pattern1D.default(), interface=interface)

Temp CIF: /tmp/easydiffraction_temp.cif


We can load up some experimental data

In [4]:
file_path = 'PbSO4_xrays_short.xye'
data_x, data_y, data_e = np.loadtxt(file_path, unpack=True)
data_set = xr.Dataset()
data_set.easyCore.add_coordinate('tth', data_x)
data_set.easyCore.add_variable('I', ['tth'], data_y)
data_set.easyCore.sigma_attach('I', data_e)


# Generate the simulation y-data
data_set.easyCore.add_variable('simulated', ['tth'], interface.fit_func(data_set['tth']))
data_set

<xarray.Dataset>
Dimensions:    (tth: 4401)
Coordinates:
  * tth        (tth) float64 10.0 10.03 10.05 10.07 ... 119.9 120.0 120.0 120.0
Data variables:
    I          (tth) float64 179.0 147.0 165.0 172.0 ... 156.0 163.0 164.0 166.0
    s_I        (tth) float64 13.38 12.12 12.85 13.11 ... 12.49 12.77 12.81 12.88
    simulated  (tth) float64 0.0 0.0 0.0 0.0 ... 5.036e-27 5.534e-27 4.583e-27
Attributes:
    name:         
    description:  
    url:          
    units:        {'tth': <Unit('dimensionless')>, 'I': <Unit('dimensionless'...

In [5]:
data_set.hvplot(y=['I', 'simulated'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

We do not have the correct experimental parameters..

In [6]:
S.parameters.wavelength = 1.54
S.parameters.u_resolution = 0.031
S.parameters.v_resolution = -0.052
S.parameters.w_resolution = 0.032
S.parameters.x_resolution = 0.015
S.parameters.y_resolution = 0.0

data_set.easyCore.add_variable('simulated', ['tth'], interface.fit_func(data_set['tth']))
data_set.hvplot(y=['I', 'simulated'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

Now we need to set the background

In [7]:
from easyDiffractionLib.Elements.Backgrounds.Point import PointBackground, BackgroundPoint

bg = PointBackground(linked_experiment='PbSO4')
bg.append(BackgroundPoint.from_pars(data_x[0], 166))
bg.append(BackgroundPoint.from_pars(16, 36))
bg.append(BackgroundPoint.from_pars(50, 120))
bg.append(BackgroundPoint.from_pars(100, 100))
bg.append(BackgroundPoint.from_pars(data_x[-1], 164))
print(bg)

S.set_background(bg)
print(S.backgrounds)

Background of 5 points.
Collection of 1 backgrounds.


In [8]:
data_set.easyCore.add_variable('simulated', ['tth'], interface.fit_func(np.array(data_set['tth'])))
data_set.hvplot(y=['I', 'simulated'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

Select CrysFML calculator

In [9]:
print(interface.available_interfaces)
print(interface.current_interface_name)
interface.switch('CrysFML')
S._updateInterface()
print(interface.current_interface_name)

['CrysPy', 'CrysFML', 'GSAS-II']
CrysPy
CrysFML


In [10]:
data_set.easyCore.add_variable('simulated', ['tth'], interface.fit_func(np.array(data_set['tth'])))
data_set.hvplot(y=['I', 'simulated'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

Change scale manually

In [11]:
S.pattern.scale = 0.1

data_set.easyCore.add_variable('simulated', ['tth'], interface.fit_func(np.array(data_set['tth'])))
data_set.hvplot(y=['I', 'simulated'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

## Fitting to the data

Initalize the fitting engine and apply a few constraints

In [12]:
f = Fitter(S, interface.fit_func)

# Vary the scale and the BG points
S.pattern.scale.fixed = False
S.pattern.zero_shift.fixed = False
#S.parameters.resolution_u.fixed = False
#S.parameters.resolution_v.fixed = False
#S.parameters.resolution_w.fixed = False
#S.parameters.resolution_x.fixed = False
#S.backgrounds[0][0].y.fixed = False
#S.backgrounds[0][1].y.fixed = False
#S.backgrounds[0][2].y.fixed = False
#S.backgrounds[0][3].y.fixed = False
#S.backgrounds[0][4].y.fixed = False

Select bumps minimizer

In [13]:
print("available minimizers:", f.available_engines)
print()
print("current minimizer:", f.current_engine.name)
print("available methods of current minimizer:", f.available_methods())
print()
print("switch minimizer")
f.switch_engine('bumps')
f_method = 'lm'
print("current minimizer:", f.current_engine.name)
print("available methods of current minimizer:", f.available_methods())

available minimizers: ['lmfit', 'bumps', 'DFO_LS']

current minimizer: lmfit
available methods of current minimizer: ['leastsq', 'least_squares', 'differential_evolution', 'basinhopping', 'ampgo', 'nelder', 'lbfgsb', 'powell', 'cg', 'newton', 'cobyla', 'bfgs']

switch minimizer
current minimizer: bumps
available methods of current minimizer: ['amoeba', 'de', 'dream', 'newton', 'lm', 'mp', 'pt']


Perform the fit

In [14]:
result = data_set['I'].easyCore.fit(f, fit_kwargs={'weights':1/data_e, 'method':f_method})

In [15]:
if result.success:
    print("The fit has been successful: {}".format(result.success))
    print("The gooodness of fit is: {}".format(result.goodness_of_fit))
    
data_set['best_fit'] = result.y_calc

The fit has been successful: True
The gooodness of fit is: 1507315286220.7224


In [16]:
data_set.hvplot(y =['I', 'best_fit'])

:NdOverlay   [Variable]
   :Curve   [tth]   (value)

In [17]:
print(f'Scale: {S.pattern.scale}')
print(f'Scale: {S.pattern.zero_shift}')

Scale: <Parameter 'scale': 0.2216+/-0.0000, bounds=[-inf:inf]>
Scale: <Parameter 'zero_shift': 0.0148+/-0.0000 deg, bounds=[-inf:inf]>
